In [1]:
import re, string, unicodedata
import nltk
import contractions # expanding contractions
import inflect # natural language related tasks of generating plurals, singular nouns, etc.
from nltk import word_tokenize, sent_tokenize
from nltk.corpus import stopwords
from nltk.stem import LancasterStemmer, WordNetLemmatizer
from nltk.tokenize import TweetTokenizer
from pymongo import MongoClient
import string


#nltk.download('punkt')
#nltk.download('stopwords')
#nltk.download('wordnet')

[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\Stagiaire2014\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\Stagiaire2014\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package wordnet to
[nltk_data]     C:\Users\Stagiaire2014\AppData\Roaming\nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


True

## Connect to database

In [2]:
try:
    client = MongoClient('localhost', 27017) # host, port
except ConnectionFailure as e:
    sys.stderr.write("Could not connect to MongoDB: %s" % e)
    sys.exit(1)

# create database tweet_database
db = client.tweets_database

# delete collection
#db.tweets.drop()

# create collection tweets (eq. of a table in relational database)
tweets = db.raw_tweets

# number of tweets
print("total number of tweets:", tweets.count())
print("number of english tweets:", tweets.find({'lang': 'en'}).count())

total number of tweets: 3364001
number of english tweets: 2706977


### import path to use preprocess library (only for jupyter notebook)

In [3]:
import sys
path = 'D:\A_AHNE1\Tweet-Classification-Diabetes-Distress\preprocess'

if path not in sys.path:
    sys.path.insert(0, path)
sys.path

#sys.path.remove(path)
#sys.path

['D:\\A_AHNE1\\Tweet-Classification-Diabetes-Distress\\preprocess',
 '',
 'c:\\users\\stagiaire2014\\miniconda3\\envs\\deepscience\\python35.zip',
 'c:\\users\\stagiaire2014\\miniconda3\\envs\\deepscience\\DLLs',
 'c:\\users\\stagiaire2014\\miniconda3\\envs\\deepscience\\lib',
 'c:\\users\\stagiaire2014\\miniconda3\\envs\\deepscience',
 'c:\\users\\stagiaire2014\\miniconda3\\envs\\deepscience\\lib\\site-packages',
 'c:\\users\\stagiaire2014\\miniconda3\\envs\\deepscience\\lib\\site-packages\\xgboost-0.7-py3.5.egg',
 'c:\\users\\stagiaire2014\\miniconda3\\envs\\deepscience\\lib\\site-packages\\IPython\\extensions',
 'C:\\Users\\Stagiaire2014\\.ipython']

### import class for the preprocessing part

In [5]:
from preprocess import Preprocess
prep = Preprocess()

[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\Stagiaire2014\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\Stagiaire2014\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package wordnet to
[nltk_data]     C:\Users\Stagiaire2014\AppData\Roaming\nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


### get first 1000 tweets

In [17]:
count = 1
tweets_list = ["I love:D python 😄 :-)"] # add sample tweet to illustrate emoticons and emojis 
for tweet in tweets.find({'lang': 'en'}):
    
    tweet = prep.get_text(tweet)
    tweets_list.append(tweet)
    count += 1

    if (count == 10000):
        break

### Preprocess tweets

In [12]:
for tweet in tweets_list:

    print("")
    print("")
    print("----------ORIGINAL----------:")
    print(tweet)
    print("")
    
    tweet = prep.replace_contractions(tweet)
    tweet = prep.replace_special_words(tweet)
    tweet = prep.replace_hashtags_URL_USER(tweet)
    tweet = prep.tokenize(tweet)
    tweet = prep.remove_punctuation(tweet)
    print("-----REPLACED CONTRACTIONS, HASHTAGS, URLs AND USER MENTIONS, TOKENISE; REMOVE PUNCTUATIONS----:")
    print(tweet)
    print("")
    
    tweet = prep.preprocess_emojis(tweet)
    tweet = prep.preprocess_emoticons(tweet)
    tweet = prep.remove_non_ascii(tweet)
    tweet = prep.to_lowercase(tweet)
    tweet = prep.replace_numbers(tweet)
    #print("-----REPLACE EMOJIS AND EMOTICONS; REMOVE NON ASCII, TO LOWERCASE, REPLACE NUMBERS------:")
    #print(tweet)
    #print("")
    
    tweet = prep.remove_stopwords(tweet)
    tweet = prep.lemmatize_verbs(tweet)
    tweet = prep.stem_words(tweet)
    print("----------REMOVE STOPWORDS, LEMMATIZE AND STEM-------------:")
    print(tweet)
    print("")
    
    #tweets_list.append(tweet)
    #print(tweet)
    




----------ORIGINAL----------:
I love:D python 😄 :-)

-----REPLACED CONTRACTIONS, HASHTAGS, URLs AND USER MENTIONS, TOKENISE; REMOVE PUNCTUATIONS----:
['I', 'love', ':D', 'python', '😄', ':-)']

----------REMOVE STOPWORDS, LEMMATIZE AND STEM-------------:
['love', 'EMOT_LAUGH', 'python', 'EMOT_LAUGH', 'EMOT_SMILE']



----------ORIGINAL----------:
NEW! Reduce Age-Related Diseases! Linked to reducing cancer, diabetes, and cardiovascular disease. MORE INFO @… https://t.co/z2zdz1uYsd

-----REPLACED CONTRACTIONS, HASHTAGS, URLs AND USER MENTIONS, TOKENISE; REMOVE PUNCTUATIONS----:
['NEW', 'Reduce', 'Age-Related', 'Diseases', 'Linked', 'to', 'reducing', 'cancer', 'diabetes', 'and', 'cardiovascular', 'disease', 'MORE', 'INFO', 'URL']

----------REMOVE STOPWORDS, LEMMATIZE AND STEM-------------:
['new', 'reduc', 'age-rel', 'diseas', 'link', 'reduc', 'cancer', 'diabet', 'cardiovascular', 'diseas', 'info', 'URL']



----------ORIGINAL----------:
RT @shanselman: Just got labs back from my 3 mont



----------ORIGINAL----------:
Our researchers @UniversityLeeds tell you how sleep affects glucose levels 9pm tonight @BBCOne #TruthAboutSleep… https://t.co/KDH75iO0nK

-----REPLACED CONTRACTIONS, HASHTAGS, URLs AND USER MENTIONS, TOKENISE; REMOVE PUNCTUATIONS----:
['Our', 'researchers', 'USER', 'tell', 'you', 'how', 'sleep', 'affects', 'glucose', 'levels', '9pm', 'tonight', 'USER', 'TruthAboutSleep', 'URL']

----------REMOVE STOPWORDS, LEMMATIZE AND STEM-------------:
['research', 'USER', 'tell', 'sleep', 'affect', 'glucos', 'level', '9pm', 'tonight', 'USER', 'truthaboutsleep', 'URL']



----------ORIGINAL----------:
A computer-generated physician, now under development, explains diabetes and cholesterol test results to would-be pa https://t.co/PBcAoNyNcp

-----REPLACED CONTRACTIONS, HASHTAGS, URLs AND USER MENTIONS, TOKENISE; REMOVE PUNCTUATIONS----:
['A', 'computer-generated', 'physician', 'now', 'under', 'development', 'explains', 'diabetes', 'and', 'cholesterol', 'test', 'results



----------ORIGINAL----------:
Will it work for humans?: Scientists cure type 1 diabetes (in mice) using gene transfer https://t.co/S9AiNfHhYG

-----REPLACED CONTRACTIONS, HASHTAGS, URLs AND USER MENTIONS, TOKENISE; REMOVE PUNCTUATIONS----:
['Will', 'it', 'work', 'for', 'humans', 'Scientists', 'cure', 'type', '1', 'diabetes', 'in', 'mice', 'using', 'gene', 'transfer', 'URL']

----------REMOVE STOPWORDS, LEMMATIZE AND STEM-------------:
['work', 'human', 'scientist', 'cure', 'type', 'one', 'diabet', 'mice', 'use', 'gene', 'transfer', 'URL']



----------ORIGINAL----------:
Hey hey hey heyyyy feeed us! We are starving!!!!
* notice the one with fat belly and diabetes... https://t.co/hq81FVU2Ni

-----REPLACED CONTRACTIONS, HASHTAGS, URLs AND USER MENTIONS, TOKENISE; REMOVE PUNCTUATIONS----:
['Hey', 'hey', 'hey', 'heyyyy', 'feeed', 'us', 'We', 'are', 'starving', 'notice', 'the', 'one', 'with', 'fat', 'belly', 'and', 'diabetes', 'URL']

----------REMOVE STOPWORDS, LEMMATIZE AND STEM--------


-----REPLACED CONTRACTIONS, HASHTAGS, URLs AND USER MENTIONS, TOKENISE; REMOVE PUNCTUATIONS----:
['RT', 'USER', 'Fluoride', 'has', 'been', 'linked', 'to', 'calcification', 'of', 'the', 'pineal', 'gland', 'lower', 'IQ', 'cancer', 'endocrine', 'disruption', 'diabetes', 'kidney']

----------REMOVE STOPWORDS, LEMMATIZE AND STEM-------------:
['rt', 'USER', 'fluorid', 'link', 'calcif', 'pineal', 'gland', 'lower', 'iq', 'cancer', 'endocrin', 'disrupt', 'diabet', 'kidney']



----------ORIGINAL----------:
Mum's fury after diabetic son refused food at McDonald's despite suga - Sunday Mercury  https://t.co/c4hei5E81u

-----REPLACED CONTRACTIONS, HASHTAGS, URLs AND USER MENTIONS, TOKENISE; REMOVE PUNCTUATIONS----:
["Mum's", 'fury', 'after', 'diabetic', 'son', 'refused', 'food', 'at', "McDonald's", 'despite', 'suga', 'Sunday', 'Mercury', 'URL']

----------REMOVE STOPWORDS, LEMMATIZE AND STEM-------------:
['mum', 'furi', 'diabet', 'son', 'refus', 'food', 'mcdonald', 'despit', 'suga', 'sunday', '

['american', 'stop', 'drink', 'soda', 'everi', 'day', 'two', 'million', 'case', 'diabet', 'could', 'prevent', 'two thousand and twenti']



----------ORIGINAL----------:
RT @UberFacts: If Americans stopped drinking soda every day, 2 million cases of diabetes could be prevented by 2020.

-----REPLACED CONTRACTIONS, HASHTAGS, URLs AND USER MENTIONS, TOKENISE; REMOVE PUNCTUATIONS----:
['RT', 'USER', 'If', 'Americans', 'stopped', 'drinking', 'soda', 'every', 'day', '2', 'million', 'cases', 'of', 'diabetes', 'could', 'be', 'prevented', 'by', '2020']

----------REMOVE STOPWORDS, LEMMATIZE AND STEM-------------:
['rt', 'USER', 'american', 'stop', 'drink', 'soda', 'everi', 'day', 'two', 'million', 'case', 'diabet', 'could', 'prevent', 'two thousand and twenti']



----------ORIGINAL----------:
@GilmerHealthLaw @lollydaggle If my number is called one day because of lack of insulin access, I will gladly do th… https://t.co/ynSa1o7V2f

-----REPLACED CONTRACTIONS, HASHTAGS, URLs AND USER MENTIONS,

...

NEW DATA! Fighting Statin-Induced Diabetes with CoQ10. CoQ10 can greatly reduce these glucose control issues. GO…… https://t.co/sKgK1MHm0i

-----REPLACED CONTRACTIONS, HASHTAGS, URLs AND USER MENTIONS, TOKENISE; REMOVE PUNCTUATIONS----:
['NEW', 'DATA', 'Fighting', 'Statin-Induced', 'Diabetes', 'with', 'CoQ', '10', 'CoQ', '10', 'can', 'greatly', 'reduce', 'these', 'glucose', 'control', 'issues', 'GO', 'URL']

----------REMOVE STOPWORDS, LEMMATIZE AND STEM-------------:
['new', 'data', 'fight', 'statin-induc', 'diabet', 'coq', 'ten', 'coq', 'ten', 'great', 'reduc', 'glucos', 'control', 'issu', 'go', 'URL']



----------ORIGINAL----------:
RT @themediaoctopus: #DorothyHodgkin used X-rays to crack the structures of penicillin, insulin &amp; vitamin B12. #science #womenintech https:…

-----REPLACED CONTRACTIONS, HASHTAGS, URLs AND USER MENTIONS, TOKENISE; REMOVE PUNCTUATIONS----:
['RT', 'USER', 'DorothyHodgkin', 'used', 'X-rays', 'to', 'crack', 'the', 'structures', 'of', 'penicillin', 'insu


----------REMOVE STOPWORDS, LEMMATIZE AND STEM-------------:
['a1c', 'lower', 'earli', 'pregnanc', 'despit', 'gestat', 'diabet', 'diagnosi', 'bodi', 'weird']



----------ORIGINAL----------:
NEW DATA! Fighting Statin-Induced Diabetes with CoQ10. CoQ10 can greatly reduce these glucose control issues. GO…… https://t.co/r7Az0wD3yh

-----REPLACED CONTRACTIONS, HASHTAGS, URLs AND USER MENTIONS, TOKENISE; REMOVE PUNCTUATIONS----:
['NEW', 'DATA', 'Fighting', 'Statin-Induced', 'Diabetes', 'with', 'CoQ', '10', 'CoQ', '10', 'can', 'greatly', 'reduce', 'these', 'glucose', 'control', 'issues', 'GO', 'URL']

----------REMOVE STOPWORDS, LEMMATIZE AND STEM-------------:
['new', 'data', 'fight', 'statin-induc', 'diabet', 'coq', 'ten', 'coq', 'ten', 'great', 'reduc', 'glucos', 'control', 'issu', 'go', 'URL']



----------ORIGINAL----------:
10 foods that can help prevent diabetes https://t.co/fDsXupOb8y https://t.co/XIpg5gbNE3

-----REPLACED CONTRACTIONS, HASHTAGS, URLs AND USER MENTIONS, TOKENISE; RE

----------ORIGINAL----------:
RT @royalsociety: Hodgkin's ground-breaking work helped unravel the structure of insulin after 30 years study https://t.co/1ANJwNaphV https…

-----REPLACED CONTRACTIONS, HASHTAGS, URLs AND USER MENTIONS, TOKENISE; REMOVE PUNCTUATIONS----:
['RT', 'USER', "Hodgkin's", 'ground-breaking', 'work', 'helped', 'unravel', 'the', 'structure', 'of', 'insulin', 'after', '30', 'years', 'study', 'URL', 'URL']

----------REMOVE STOPWORDS, LEMMATIZE AND STEM-------------:
['rt', 'USER', 'hodgkin', 'ground-break', 'work', 'help', 'unravel', 'structur', 'insulin', 'thirti', 'year', 'studi', 'URL', 'URL']



----------ORIGINAL----------:
#diabeteshelp Encyclopedia of Natural Medicine : Your Comprehensive, User-Friendly A-to-Z...: $7.99 (0 Bids)… https://t.co/BNNFgp4Q0x #T1D

-----REPLACED CONTRACTIONS, HASHTAGS, URLs AND USER MENTIONS, TOKENISE; REMOVE PUNCTUATIONS----:
['diabeteshelp', 'Encyclopedia', 'of', 'Natural', 'Medicine', 'Your', 'Comprehensive', 'User-Friendly', 'A

Optimistic result of islet cell transplantation https://t.co/AO5IZIF8D3 #diabetes #T1DM #health

-----REPLACED CONTRACTIONS, HASHTAGS, URLs AND USER MENTIONS, TOKENISE; REMOVE PUNCTUATIONS----:
['Optimistic', 'result', 'of', 'islet', 'cell', 'transplantation', 'URL', 'diabetes', 'T1DM', 'health']

----------REMOVE STOPWORDS, LEMMATIZE AND STEM-------------:
['optimist', 'result', 'islet', 'cell', 'transplant', 'URL', 'diabet', 't1dm', 'health']



----------ORIGINAL----------:
Beneficial lipids? The Arachidonic acid-derived lipids, EETs, are associated with insulin sensitivity… https://t.co/u8BJ6xBJCS

-----REPLACED CONTRACTIONS, HASHTAGS, URLs AND USER MENTIONS, TOKENISE; REMOVE PUNCTUATIONS----:
['Beneficial', 'lipids', 'The', 'Arachidonic', 'acid-derived', 'lipids', 'EETs', 'are', 'associated', 'with', 'insulin', 'sensitivity', 'URL']

----------REMOVE STOPWORDS, LEMMATIZE AND STEM-------------:
['benefici', 'lipid', 'arachidon', 'acid-deriv', 'lipid', 'eet', 'associ', 'insulin', 's

['oman', 'well', 'prevent', 'diabet', 'heart', 'diseas', 'URL', 'heartdiseas']



----------ORIGINAL----------:
@MoveForwardMult they don't need diabetes. bye @CocaCola

-----REPLACED CONTRACTIONS, HASHTAGS, URLs AND USER MENTIONS, TOKENISE; REMOVE PUNCTUATIONS----:
['USER', 'they', 'do', 'not', 'need', 'diabetes', 'bye', 'USER']

----------REMOVE STOPWORDS, LEMMATIZE AND STEM-------------:
['USER', 'need', 'diabet', 'bye', 'USER']



----------ORIGINAL----------:
RT @kathieallenmd: Profound ignorance of diabetes, a multifactorial disease assoc with genetics, lifestyle, race, age, &amp; others. Lifes… 

-----REPLACED CONTRACTIONS, HASHTAGS, URLs AND USER MENTIONS, TOKENISE; REMOVE PUNCTUATIONS----:
['RT', 'USER', 'Profound', 'ignorance', 'of', 'diabetes', 'a', 'multifactorial', 'disease', 'assoc', 'with', 'genetics', 'lifestyle', 'race', 'age', 'others', 'Lifes']

----------REMOVE STOPWORDS, LEMMATIZE AND STEM-------------:
['rt', 'USER', 'profound', 'ignor', 'diabet', 'multifactori', 

### List of english stopwords that are deleted

In [49]:
stopwords.words('english')

['i',
 'me',
 'my',
 'myself',
 'we',
 'our',
 'ours',
 'ourselves',
 'you',
 "you're",
 "you've",
 "you'll",
 "you'd",
 'your',
 'yours',
 'yourself',
 'yourselves',
 'he',
 'him',
 'his',
 'himself',
 'she',
 "she's",
 'her',
 'hers',
 'herself',
 'it',
 "it's",
 'its',
 'itself',
 'they',
 'them',
 'their',
 'theirs',
 'themselves',
 'what',
 'which',
 'who',
 'whom',
 'this',
 'that',
 "that'll",
 'these',
 'those',
 'am',
 'is',
 'are',
 'was',
 'were',
 'be',
 'been',
 'being',
 'have',
 'has',
 'had',
 'having',
 'do',
 'does',
 'did',
 'doing',
 'a',
 'an',
 'the',
 'and',
 'but',
 'if',
 'or',
 'because',
 'as',
 'until',
 'while',
 'of',
 'at',
 'by',
 'for',
 'with',
 'about',
 'against',
 'between',
 'into',
 'through',
 'during',
 'before',
 'after',
 'above',
 'below',
 'to',
 'from',
 'up',
 'down',
 'in',
 'out',
 'on',
 'off',
 'over',
 'under',
 'again',
 'further',
 'then',
 'once',
 'here',
 'there',
 'when',
 'where',
 'why',
 'how',
 'all',
 'any',
 'both',
 'each

In [49]:
# additional text cleaning

# Locate and correct common typos and misspellings
# Handling numbers and dates inside the text



In [50]:
prep.Constant_words

['URL',
 'USER',
 'EMOT_SMILE',
 'EMOT_LAUGH',
 'EMOT_LOVE',
 'EMOT_WINK',
 'EMOT_SAD_ANGRY',
 'EMOT_SURPRISED',
 'EMOT_CRY']

In [57]:
tweet="I 马克 can't:D python as @charlie 94 singing in the rain ... #smile 😄 :-) \
       https://t.co/gjW9CHMzfH !!"
tweet.encode('ascii', 'ignore').decode('utf-8', 'ignore')

"I  can't:D python as @charlie 94 singing in the rain ... #smile  :-)        https://t.co/gjW9CHMzfH !!"

In [58]:
sys.stdout.encoding

'UTF-8'

In [6]:
tweet = "Woman with type 1 diabetes still off insulin one year after cell "
prep.replace_special_words(tweet)

'Woman with type1 diabetes still off insulin one year after cell '